In [ ]:
'''
ASI3 algorithm

Author: Junshen Lu
Contact: lu@iup.physik.uni-bremen.de

Purpose:
1.Applies weather correction on the AMSR-E brightness temperatures.
2.Retrieves sea ice concentration from the corrected 89 GHz brightness temperatures.


Input data:
1. AMSR-E Level 2A brightness temperatures
2. Geophysical parameters (total water vapor, cloud liquid water, wind speed, surface temperature) retrieved by an optimal estimation method (Scarlat 2017).

Output data:
1. Weather corrected brightness temperatures
2. Sea ice concentration

'''

In [1]:
# Standard library imports
import os,sys,glob
import numpy as np
import pandas as pd


# Local application imports
from wentz_rtm import wentz_rtm
from asi_lib import poly3d, asi_alg

In [2]:
# read input data
cwd=os.getcwd()

version='10c'
refsic='SIC0'

oemfname = os.path.join(cwd,'input_oem.asc')
tbfname = os.path.join(cwd,'input_amsre.asc')


#antwv;anwsp;anskt;fcclw;eratwv;erawsp;eraskt;efcclw
oemclist=['lon','lat','wsp','twv','lwp','sst','ist','sic','fmy','flag','ignore1','day','month','ignore4']
oem = pd.read_csv(oemfname,delimiter=' ',header=None,na_values=np.nan,names=oemclist)


tbclist=['6v','6h','10v','10h','18v','18h','23v','23h','36v','36h','89v','89h']
tb=pd.read_csv(tbfname,delimiter=' ',header=None,na_values=np.nan,names=tbclist)



In [3]:
# convert month and day to integer
oem.month=oem.month.astype(int)
oem.day=oem.day.astype(int)


In [4]:
# apply atm correction
tbm=list()
for i,row in oem.iterrows():
    tbm0=wentz_rtm(month=int(row['month']),day=int(row['day']),W=0,V=0,L=0,T_ow=271.15,T_is=250,C_is=row['sic'],C_MY=row['fmy']*row['sic'])
    tbma=wentz_rtm(month=int(row['month']),day=int(row['day']),W=row['wsp'],V=row['twv'],L=row['lwp'],T_ow=row['sst'],T_is=row['ist'],C_is=row['sic'],C_MY=row['fmy']*row['sic'])
    tbm.append(tbma-tbm0)

In [5]:
# compute corrected tb
tbm=np.array(tbm)

tb['h6c']=tb['6h']-tbm[:,1]
tb['v6c']=tb['6v']-tbm[:,0]
tb['h10c']=tb['10h']-tbm[:,3]
tb['v10c']=tb['10v']-tbm[:,2]
tb['h18c']=tb['18h']-tbm[:,5]
tb['v18c']=tb['18v']-tbm[:,4]
tb['h23c']=tb['23h']-tbm[:,7]
tb['v23c']=tb['23v']-tbm[:,6]
tb['h36c']=tb['36h']-tbm[:,9]
tb['v36c']=tb['36v']-tbm[:,8]
tb['h89c']=tb['89h']-tbm[:,11]
tb['v89c']=tb['89v']-tbm[:,10]


In [8]:
# compute ASI3 ice concentration

# define tie points
p0_asi3=80.
p1_asi3=14.

# compute 89 GHz polarization difference
p89=tb['v89c']-tb['h89c']
gr36=(tb['v36c']-tb['v18c'])/(tb['v36c']+tb['v18c'])

# ASI3 ice concentration, without 0-100% boundary, without weather filters
sic_asi3_nb = asi_alg(p89,p0_asi3,p1_asi3,boundary=0)

# ASI3 ice concentration, with 0-100% boundary, without weather filters
sic_asi3_nwf = asi_alg(p89,p0_asi3,p1_asi3,boundary=1)

# ASI3 ice concentration, with 0-100% boundary, with weather filters
wf_asi3=(gr36>=0.07)
sic_asi3_wf=sic_asi3_nwf.copy()
sic_asi3_wf[wf_asi3]=0.